In [2]:
import numpy as np
import pandas as pd
import plotly.express as px
import math
import plotly.io as pio

pio.renderers.default='notebook'
pd.options.plotting.backend = "plotly"

# Utilities

In [3]:
# utils
def plot_state_vs_time(df):    
    fig = df.plot()
    fig.update_layout(height=700)
    fig.show()

## Forward Euler Numerical Integrator
$\underline{X(t_{k + 1})} = \underline{X(t_{k})} + dt\underline{\dot{X(t_{k})}}$

In [4]:
def euler_integrator(x_0, t_0, t_n, dt, dx):
    x = x_0
    t = t_0
    
    yield (x, t)
    
    while t <= t_n:
        # eval x_k+1 using x_k and t_k
        x = x + dt * dx(x, t)
        
        # t increament to t_k+1
        t = t + dt
        
        yield (x, t)

## Runga Kutta 4 Numerical Integrator
https://en.wikipedia.org/wiki/Runge%E2%80%93Kutta_methods

$\underline{X(t_{k + 1})} = \underline{X(t_{k})} + dt(k_1 + 2k_2 + 2k_3 + k_4)\frac{1}{6}$

where:  
$f(x,t) = \underline{\dot{X(t_{k})}}$  
$k_1 = f(\underline{x_k}, t_k)$  
$k_2 = f(\underline{x_k} + dt\frac{k_1}{2}, t_k + \frac{dt}{2})$  
$k_3 = f(\underline{x_k} + dt\frac{k_2}{2}, t_k + \frac{dt}{2})$  
$k_4 = f(\underline{x_k} + dt k_3, t_k + dt)$ 

In [5]:
def rk4_integrator(x_0, t_0, t_n, dt, dx):
    x = x_0
    t = t_0
    
    yield (x, t)
    
    while t <= t_n:
        # eval x_k+1 using x_k and t_k
        k1 = dx(x, t)
        k2 = dx(x + dt * k1 / 2, t + dt / 2)
        k3 = dx(x + dt * k2 / 2, t + dt / 2)
        k4 = dx(x + dt * k3, t + dt)
        
        x = x + dt * (k1 + 2*k2 + 2*k3 + k4) * (1/6)
        
        # t increament to t_k+1
        t = t + dt
        
        yield (x, t)

# Assignment Questions

## Q2. b) 
$\ddot{x}(t) = -2x(t) - 10\dot{x}(t)$

### ans:

Let 

$x(t) = x_1(t)$ 

$\dot{x}(t) = x_2(t)$

Let state vector $\textbf{X} = [x_1, x_2]^T$

We can rewrite the equations given in the question as the following system of 2 first order O.D.E.s.

$\dot{x_1}(t) = x_2(t)$

$\dot{x_2}(t) = -2x_1(t) - 10x_2(t)$

In [6]:
A = np.array(
    [
        [0, 1],
        [-2, -10]
    ]
)

def dx(X, t = None):
    return A@X

X_0 = np.array(
    [
        [1],
        [0]
    ]
)

T = 20

# Euler
dt = 1e-3 # delta time (seconds)
state_time = []
state_integrator = euler_integrator(X_0, 0, T, dt, dx)
for x, t in state_integrator:
    state_time.append({"X_1 (Euler)": x[0][0], "X_2 (Euler)": x[1][0], "Time": t})
e_state_time_df = pd.DataFrame(state_time).set_index("Time")

# RK4
dt = 1e-3 # delta time (seconds)
state_time = []
state_integrator = rk4_integrator(X_0, 0, T, dt, dx)
for x, t in state_integrator:
    state_time.append({"X_1 (RK4)": x[0][0], "X_2 (RK4)": x[1][0], "Time": t})
r_state_time_df = pd.DataFrame(state_time).set_index("Time")

state_time_df = pd.concat([r_state_time_df, e_state_time_df])

plot_state_vs_time(state_time_df)